In [52]:
import re
import numpy as np
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.tokenize import sent_tokenize
from nltk.stem.porter import PorterStemmer
from nltk.stem.wordnet import WordNetLemmatizer
from nltk.sentiment.vader import SentimentIntensityAnalyzer
from sklearn.naive_bayes import GaussianNB
from sklearn import svm
from gensim.models import Word2Vec 
from sklearn import tree
from sklearn.neighbors import KNeighborsClassifier

In [53]:
tweets = []
index = []
labels = []

In [54]:
stemmer = PorterStemmer()
lmtzr = WordNetLemmatizer()

def stem_tokens(tokens, stemmer):
    stemmed = []
    for item in tokens:
        stemmed.append(stemmer.stem(item))
    return stemmed

def wordtovec(trainingdata):
    model = Word2Vec(trainingdata, min_count=1)
    model.save('model.bin')
    print(model)
    return model
    

def lem_tokens(tokens, lmtzr):
    lemmed = []
    for item in tokens:
        lemmed.append(lmtzr.lemmatize(item))
    return lemmed

def zerolistmaker(n):
    listofzeros = [0] * n
    return listofzeros

def sentencevector(sentence):
    vectormapping=[]
    trainvector=zerolistmaker(100)
    k=1
    for word in sentence:
        if word in list(model.wv.key_to_index):
            vectormapping=model.wv[word]
            trainvector+=vectormapping
        k+=1
    trainvector[:] = [x / k for x in trainvector]
    print(trainvector)
    return trainvector

In [55]:
stop_words = set(stopwords.words('english'))
stop_words.add(',')
stop_words.add('.')
stop_words.add('...')
stop_words.add('..')
stop_words.add("'s")

In [56]:
with open("SemEval2018-T3-train-taskA.txt", encoding="utf8") as ins:
    tweets = []
    for line in ins:
        new = re.split(r'\t+', line.rstrip('\t'))
        newString =new[2].rstrip('\n')
        newString = re.sub(r"http\S+", "", newString)
        newString = re.sub(r"@\S+ ", "", newString)
        newString = re.sub(r"#", "", newString)
        newString = re.sub('(.)([A-Z][a-z]+)', r'\1 \2', newString)
        newString = re.sub('([a-z0-9])([A-Z])', r'\1 \2', newString).lower()
        firstString = newString
        data = word_tokenize(firstString)
        stems = stem_tokens(data, stemmer)
        lems = lem_tokens(data, lmtzr)
        tweets.append(lems)
model=wordtovec(tweets)

Word2Vec(vocab=9757, vector_size=100, alpha=0.025)


In [57]:
with open("SemEval2018-T3-train-taskA.txt", encoding="utf8") as ins:
    array = []
    X=[]
    for line in ins:
        new = re.split(r'\t+', line.rstrip('\t'))
        index.append(new[0])
        labels.append(new[1])
        label=new[1]
        newString =new[2].rstrip('\n')
        newString = re.sub(r"http\S+", "", newString)
        newString = re.sub(r"@\S+ ", "", newString)
        newString = re.sub(r"#", "", newString)
        newString = re.sub('(.)([A-Z][a-z]+)', r'\1 \2', newString)
        newString = re.sub('([a-z0-9])([A-Z])', r'\1 \2', newString).lower()
        lastString = word_tokenize(newString)
        filtered_sentence = [w for w in lastString if not w in stop_words]
        stems = stem_tokens(filtered_sentence, stemmer)
        lems = lem_tokens(filtered_sentence, lmtzr)
        embeddedvector=sentencevector(lems)
        array.extend(embeddedvector)
print(len(tweets))
print(len(embeddedvector))
data= np.reshape(array, (len(tweets), len(embeddedvector)))  

[-0.02734161  0.0939437   0.01259446  0.00278228  0.0235062  -0.16978537
  0.06793675  0.21497343 -0.10577967 -0.10057114 -0.02158042 -0.16177
 -0.01365244  0.01903521  0.04009855 -0.07556767  0.02435875 -0.1087438
 -0.04148484 -0.18221574  0.06503549  0.05560453  0.07373326 -0.01928377
 -0.016719   -0.00977997 -0.07135853 -0.04214982 -0.1128904  -0.00891454
  0.10795761 -0.00139229  0.04691785 -0.08526736 -0.04565885  0.115419
  0.02750231 -0.03990843 -0.08536389 -0.12592415  0.01200908 -0.08488822
 -0.0740088   0.02415145  0.0652911  -0.05307477 -0.06465171 -0.03429497
  0.04798494  0.06843563  0.03060454 -0.08607232 -0.02121039 -0.03904323
 -0.05137953  0.04535139  0.06947235  0.01172778 -0.05194898  0.07236731
  0.03297734  0.01688858  0.06364964  0.01558821 -0.10276959  0.10984919
  0.02953075  0.09794064 -0.11516524  0.1250167  -0.05582766  0.06317313
  0.08802133  0.02193118  0.11942549  0.05069719  0.0144453  -0.00478999
 -0.06216245  0.01206627 -0.08561008  0.00271515 -0.09864

[-0.13385551  0.3831027   0.08197814  0.02102384  0.11468671 -0.66895512
  0.29304143  0.89904003 -0.44946021 -0.40573358 -0.09253328 -0.66697688
 -0.08253705  0.10131697  0.18113016 -0.27729923  0.11025188 -0.40828192
 -0.16189135 -0.75144576  0.27681886  0.22205443  0.294073   -0.11160233
 -0.08189395 -0.0262425  -0.2749569  -0.1732914  -0.43794017 -0.02932172
  0.44353433 -0.00775763  0.18295119 -0.3504633  -0.19271153  0.47330956
  0.11216056 -0.15147887 -0.35201862 -0.49108307  0.07275824 -0.363682
 -0.28091796  0.07850374  0.26363566 -0.18826156 -0.23679898 -0.14197945
  0.18653499  0.28165471  0.13055106 -0.37045602 -0.08715223 -0.15840439
 -0.20170358  0.18284032  0.26236432  0.04037642 -0.22041626  0.28574844
  0.12362258  0.08068187  0.24741489  0.05932933 -0.4026372   0.44027845
  0.13363964  0.38880579 -0.44977875  0.5269476  -0.2190211   0.22880154
  0.37981092  0.09690155  0.48385938  0.19808684  0.07528301 -0.03676412
 -0.22092826  0.0169547  -0.3360311  -0.00289433 -0.3

[-0.07630417  0.222705    0.04686875  0.01237943  0.06450272 -0.39472747
  0.1753035   0.52674705 -0.26479195 -0.23854235 -0.05316404 -0.38869085
 -0.0417368   0.05854397  0.10750324 -0.16868351  0.06327313 -0.24466044
 -0.09189507 -0.44269983  0.16458755  0.13173814  0.17311855 -0.06168428
 -0.05142152 -0.01351501 -0.16138612 -0.09802644 -0.26131238 -0.02091407
  0.26234259 -0.00348198  0.11056536 -0.20679455 -0.10941294  0.27863946
  0.06560104 -0.08708998 -0.21293773 -0.29286443  0.04009135 -0.21663845
 -0.16762705  0.04623173  0.15489419 -0.11318236 -0.13846861 -0.080295
  0.11194781  0.16470136  0.07488738 -0.21947919 -0.05124573 -0.09590366
 -0.1183982   0.10272611  0.15278698  0.02215703 -0.13103142  0.16651329
  0.07828923  0.04686392  0.14721341  0.04004721 -0.23515206  0.25539585
  0.07903139  0.23351772 -0.26546406  0.3073772  -0.12933447  0.13602906
  0.22409362  0.05847706  0.28723593  0.1216737   0.04611286 -0.02341385
 -0.1330777   0.00785285 -0.1960009  -0.00215792 -0.2

  2.96964413e-01 -2.51043462e-01  4.42257715e-02 -1.82606372e-02]
[-8.97938272e-02  2.64841075e-01  5.54536599e-02  1.33476062e-02
  6.44065174e-02 -4.80318249e-01  2.09133773e-01  6.37107578e-01
 -3.17907348e-01 -2.90174173e-01 -7.20227310e-02 -4.72745897e-01
 -3.96254525e-02  7.16421335e-02  1.16899411e-01 -2.15691676e-01
  7.68174406e-02 -3.10384764e-01 -1.09007290e-01 -5.40375295e-01
  1.93748875e-01  1.65158418e-01  2.03041984e-01 -6.23814789e-02
 -6.40292921e-02 -1.40853311e-02 -1.92763713e-01 -1.22319526e-01
 -3.17993356e-01 -2.94623448e-02  3.24293728e-01  5.62075584e-04
  1.39848787e-01 -2.52091307e-01 -1.33900764e-01  3.36169428e-01
  7.17355376e-02 -1.14511190e-01 -2.58956316e-01 -3.74670263e-01
  3.09065470e-02 -2.54779926e-01 -1.99250822e-01  5.40600770e-02
  1.93701215e-01 -1.51382487e-01 -1.78466157e-01 -1.04423886e-01
  1.47064824e-01  2.04709309e-01  8.58589909e-02 -2.53932710e-01
 -6.85714344e-02 -1.24193616e-01 -1.53299645e-01  1.19185462e-01
  1.83982151e-01  1.6893

  1.16151613e-01 -1.01323445e-01  2.19425914e-02 -2.99780056e-02]
[-4.75970970e-03  1.18555085e-02  7.00435485e-04  4.35451278e-04
  5.50917629e-03 -2.79693256e-02  1.11543873e-02  4.10591811e-02
 -2.42196520e-02 -2.29950082e-02 -1.72678350e-03 -2.95458219e-02
 -1.20718433e-03  1.75019893e-03  7.62401187e-03 -1.35084198e-02
  4.92678556e-03 -2.11990401e-02 -4.53159663e-03 -3.46659000e-02
  1.68192467e-02  8.67912965e-03  8.15050475e-03  1.50098310e-04
 -7.74359424e-03 -2.24646427e-03 -1.60147194e-02 -6.35253106e-03
 -2.38892759e-02 -1.98111000e-03  2.36893141e-02  7.82393230e-05
  8.59838879e-03 -1.45004230e-02 -8.20242718e-03  2.50174074e-02
  5.57126927e-03 -9.11591699e-03 -1.46273654e-02 -2.43789802e-02
 -1.41048678e-03 -1.95086816e-02 -1.52902898e-02  1.52966112e-03
  1.23037690e-02 -6.17500596e-03 -9.62665786e-03 -1.24698263e-02
  6.69909905e-03  1.70443266e-02  3.64324008e-03 -1.52210363e-02
 -3.03419835e-03 -6.84466768e-03 -4.77869859e-03  8.49002569e-03
  1.30918094e-02  5.4216

...

  0.08407171 -0.07272993  0.01609842 -0.02354527]
[-0.0570319   0.15798102  0.03259161  0.00051045  0.04098597 -0.283246
  0.12512616  0.37813137 -0.18968447 -0.17011852 -0.04436343 -0.2785349
 -0.0207716   0.03830939  0.07005247 -0.12081456  0.04791509 -0.18032034
 -0.06150359 -0.32264923  0.1157071   0.09473222  0.11833618 -0.04119194
 -0.0379633  -0.00773851 -0.11176381 -0.06821924 -0.18525152 -0.01504218
  0.18453199  0.00221118  0.08286605 -0.14881632 -0.0809001   0.19811092
  0.04512081 -0.06218408 -0.1586609  -0.21822419  0.0152957  -0.14990255
 -0.11467922  0.03157818  0.11337074 -0.08659338 -0.10656262 -0.05905356
  0.08790602  0.12163024  0.04783215 -0.15127178 -0.03489716 -0.07320313
 -0.08633835  0.0655254   0.1089445   0.01292545 -0.09364367  0.11913832
  0.04988503  0.03404936  0.10168199  0.02887237 -0.16814815  0.18328294
  0.04990674  0.16832819 -0.19470865  0.22047236 -0.08378882  0.10332029
  0.15967972  0.03671789  0.20597281  0.08502932  0.03885433 -0.01935958
 -0.

  0.00693085 -0.00726993  0.00023825 -0.00312627]
[-9.04365351e-02  2.79120444e-01  5.22595860e-02  1.13551437e-02
  6.86251158e-02 -5.04767802e-01  2.25702111e-01  6.68560034e-01
 -3.37964959e-01 -3.02331981e-01 -7.13598750e-02 -4.99774357e-01
 -4.86144496e-02  6.95055699e-02  1.30104061e-01 -2.25745501e-01
  7.89507125e-02 -3.22200207e-01 -1.12501182e-01 -5.68769166e-01
  2.02225769e-01  1.78718583e-01  2.15224614e-01 -6.73242065e-02
 -6.95346696e-02 -1.60055427e-02 -1.99396003e-01 -1.28953969e-01
 -3.35936046e-01 -3.20636317e-02  3.31477179e-01 -3.83706175e-04
  1.46469326e-01 -2.61430019e-01 -1.39160913e-01  3.53484896e-01
  7.86251743e-02 -1.12272850e-01 -2.71432881e-01 -3.86069008e-01
  3.49527040e-02 -2.68143288e-01 -2.08633642e-01  5.94227912e-02
  2.03740007e-01 -1.54905720e-01 -1.86916601e-01 -1.09486379e-01
  1.55740591e-01  2.18474057e-01  8.83907531e-02 -2.69109247e-01
 -6.33920466e-02 -1.33016168e-01 -1.52010582e-01  1.26918914e-01
  1.93101405e-01  2.24311225e-02 -1.6420

  0.10317538 -0.08557241  0.01455945 -0.02904751]
[-0.08978808  0.27790099  0.05685396  0.01224764  0.07540355 -0.50169836
  0.22068173  0.66742346 -0.33693138 -0.30564982 -0.07038987 -0.49709971
 -0.04734652  0.07613513  0.13101705 -0.22222147  0.07822418 -0.31715017
 -0.11061313 -0.5695551   0.20487091  0.17151525  0.21647112 -0.07087857
 -0.06884906 -0.01807934 -0.20124177 -0.13082875 -0.33671288 -0.03056209
  0.33298734 -0.00325787  0.14054903 -0.2624414  -0.1433301   0.35334753
  0.07509146 -0.1154205  -0.27035165 -0.38412811  0.03608977 -0.27150329
 -0.20902676  0.06161642  0.20386364 -0.15312037 -0.1868208  -0.10760349
  0.15615795  0.21852203  0.0899614  -0.26944849 -0.06556012 -0.13082744
 -0.15501083  0.12582319  0.19249901  0.02244535 -0.16071419  0.2092927
  0.09650726  0.0622686   0.18486455  0.0495664  -0.30328137  0.32765579
  0.09307916  0.30241088 -0.34602066  0.38833183 -0.15541672  0.18014699
  0.2839408   0.06506884  0.3641888   0.15249755  0.06124502 -0.02180762
 -

  0.04162145 -0.03742067  0.00803855 -0.01101194]
[-0.14201691  0.38809946  0.09272089  0.02664048  0.1278193  -0.6669557
  0.29277846  0.90172486 -0.44965755 -0.40815485 -0.08743877 -0.66446275
 -0.09709867  0.10181691  0.18865713 -0.25793559  0.11095978 -0.38572794
 -0.17206474 -0.75054065  0.28593756  0.21311133  0.307941   -0.12520507
 -0.07492018 -0.02424303 -0.27796627 -0.17814592 -0.43516189 -0.01867402
  0.44520065 -0.00868714  0.1778094  -0.35395859 -0.19480253  0.47252196
  0.1192593  -0.14555128 -0.34354883 -0.47010351  0.09230524 -0.37445711
 -0.28406571  0.07878916  0.25893933 -0.17734083 -0.22696703 -0.14098231
  0.16867647  0.27838827  0.13875044 -0.38389258 -0.08723956 -0.14496017
 -0.19643844  0.19209336  0.26705214  0.04856844 -0.22184916  0.29302686
  0.12379094  0.07591897  0.24641697  0.05221314 -0.39465905  0.4476192
  0.14578279  0.3752968  -0.44165464  0.53747223 -0.23074623  0.22259721
  0.3801821   0.10769267  0.48239794  0.19304416  0.07450089 -0.0394305
 -0.

  0.0962834  -0.08221316  0.01565134 -0.01224346]
3835
100


In [58]:
del index[0]
index = list(map(int, index))
del labels[0]
labels = list(map(int, labels))
del array[0]
X = data[:3700]
Y = labels[:3700]
X1 = data[-100:]
Y1 = labels[-100:]
clf = GaussianNB()
print("results of word embedding")
y_pred = clf.fit(X, Y).predict(X1)
print('the error of naive bayes classification')
print((Y1 != y_pred).sum())
print('the accuracy of naive bayes  classification')
print((Y1 == y_pred).sum())
file = open("naive-emb.txt","w") 
for item in y_pred:
  file.write("%f" %item)
  file.write("_")
file.close() 
clf1 = svm.SVC()
y_pred = clf1.fit(X, Y).predict(X1)
print('the error of svm classification')
print((Y1 != y_pred).sum())
print('the accuracy of svm  classification')
print((Y1 == y_pred).sum())
file = open("svm-emb.txt","w") 
for item in y_pred:
  file.write("%f" %item)
  file.write("_")
file.close() 
clf = tree.DecisionTreeClassifier()
y_pred= clf.fit(X, Y).predict(X1)
print('the error of svm classification')
print((Y1 != y_pred).sum())
print('the accuracy of svm  classification')
print((Y1 == y_pred).sum())
file = open("trees-emb.txt","w") 
for item in y_pred:
  file.write("%f" %item)
  file.write("_")
file.close() 
model = KNeighborsClassifier(n_neighbors=1);
model.fit(X, Y);
Y_pred=model.predict(X1);
accuracy=(Y1 ==Y_pred).sum()
print('the error of nearest neighboor classification')
print(100-accuracy)
print('the accuracy of nearest neighboor  classification')
print(accuracy)
file = open("nearest-emb.txt","w") 
for item in Y_pred:
  file.write("%f" %item)
  file.write("_")
file.close()
   


results of word embedding
the error of naive bayes classification
50
the accuracy of naive bayes  classification
50


C:\Users\Manasvi\Anaconda3\lib\site-packages\sklearn\svm\base.py:193: FutureWarning: The default value of gamma will change from 'auto' to 'scale' in version 0.22 to account better for unscaled features. Set gamma explicitly to 'auto' or 'scale' to avoid this warning.
  "avoid this warning.", FutureWarning)


the error of svm classification
58
the accuracy of svm  classification
42
the error of svm classification
47
the accuracy of svm  classification
53
the error of nearest neighboor classification
47
the accuracy of nearest neighboor  classification
53
